In [1]:
import sys
path2cpp_pkg = "/Users/mariusmahiout/Documents/repos/ising_core/build"
sys.path.append(path2cpp_pkg)
import ising

import os
os.chdir("/Users/mariusmahiout/Documents/repos/ising_core/python")
import src.utils as utils
import src.model_eval as eval
import src.isingfitter as fitter
import src.misc_plotting as plotting

os.chdir("..")


import numpy as np
import plotly
from IPython.display import display, HTML

plotly.offline.init_notebook_mode()
display(HTML(
    '<script type="text/javascript" async src="https://cdnjs.cloudflare.com/ajax/libs/mathjax/2.7.1/MathJax.js?config=TeX-MML-AM_SVG"></script>'
))

In [2]:
num_units = 200
num_sims = 30_000
num_burn = 5000 # increase to 5k

In [3]:
##############
# SIMULATION #
##############

# setting up model
beta = 1
h = np.random.uniform(-.3 * beta, .3 * beta, num_units)
J = np.random.normal(0,  beta / np.sqrt(num_units), (num_units, num_units))
for i in range(num_units):
    J[i, i] = 0
    for j in range(i+1, num_units):
        J[j, i] = J[i, j]

true_model = ising.NeqModel(J, h)

# simulating
true_sim = true_model.simulate(num_sims, num_burn)

# Gradient ascent

In [4]:
lr = 0.1
win_size = 10
tol_ml = 1e-3
max_steps = 3000

In [5]:
##############
# LIKELIHOOD #
##############

# setting up model
h_init = np.random.uniform(-1.5, 1.5, num_units)
J_init = np.random.normal(0,  1,  (num_units, num_units))
J_init = (J_init.T + J_init) * np.sqrt(2) / 2
np.fill_diagonal(J_init, 0)

ml_model = ising.NeqModel(J_init, h_init)

ml_fitter = fitter.NeqFitter(ml_model)
#ml_fitter.TAP(true_sim)

# inference
use_llh = False
ml_fitter.maximize_likelihood(
    sample=true_sim, 
    max_steps=max_steps, 
    learning_rate=lr,
    win_size = win_size,
    tolerance= tol_ml, 
    calc_llh=use_llh
)


In [6]:
plotting.convergence_plot(ml_fitter, plot_llh=use_llh, path="./analyses/neq_convergence/ml1.pdf")

Button(description='Save Figure', style=ButtonStyle())

In [7]:
nmf_model = ising.NeqModel(J_init, h_init)
nmf_fitter = fitter.NeqFitter(nmf_model)
nmf_fitter.naive_mean_field(true_sim)

tap_model = ising.NeqModel(J_init, h_init)
tap_fitter = fitter.NeqFitter(tap_model)
tap_fitter.TAP(true_sim)


In [8]:
ml_sim = ml_model.simulate(num_sims, num_burn)
nmf_sim = nmf_model.simulate(num_sims, num_burn)
tap_sim = tap_model.simulate(num_sims, num_burn)

In [9]:


labels = ["nMF", "TAP", "ML"]
metadata = utils.get_metadata(
    num_units=num_units,
    is_empirical_analysis=False,
    eq_inv_methods=labels,
    num_sims=num_sims,
    true_fields="uniform(-.3 * beta, .3 * beta); beta=1.5",
    true_couplings="normal(0,  beta / sqrt(num_units)); symmetric, beta=1.5",
    num_steps=max_steps,
    learning_rate=lr,
    is_converged=None,
    num_sims_ml=num_sims,
    num_burn_ml=num_burn,
)


analysis_name = "neq_test"
bin_width = 0
analysis_path = utils.get_analysis_path(analysis_name, num_units, bin_width)

layout_spec = {
    ("fields", "scatter"): (1, 1),
    ("means", "scatter"): (1, 2),
    ("couplings", "scatter"): (2, 1),
    ("pcorrs", "scatter"): (2, 2),
}

ising_eval = eval.IsingEval(
    analysis_path=analysis_path, 
    metadata=metadata,
    true_model=true_model,
    est_models=[nmf_model, tap_model, ml_model],
    true_sample=true_sim,
    est_samples=[nmf_sim, tap_sim, ml_sim],
    labels=labels,
    layout_spec=layout_spec
)
ising_eval.generate_plots()

    'data': [{'legendgroup': 'nMF',
              'marker': {'color': 'blue', 's…

## To-do:
- Derive formulae for moments of equilibrium sampler
- We should now be ready to start making figures. Let's start with the plots to assess the equilibrium sampler. Is it possible to do this for the NEQ sampler as well?
- Next, we'll explore the neural recordings themselves:
    - include data directory
    - adapt preprocessing.cpp for the current version
    - plot observables of the neural recordings
- At this point, we're able to plot everything we need. Time to go through the results section of the thesis, section by section, and making new plots (and getting new numerical data). Give yourself a couple of weeks for this
- Finally, we'll update the latex document with the new figures and adjust the text


Before compiler optimizations, with **50** units, **30k** samples, and **3k** steps:
- PL takes 24 min
- ML takes 16 min

## Once project is finalized
- Make public on GitHub (exclude the data)
- Get in touch with Yasser (Also, congratulate him on his new position and ask how he's doing)
- Add it to projects on website
- Perhaps make a blog post discussing your decision to revize the project
    - Got hurried at the end, and although I recieved top marks, was not happy with the final product (figures, code, etc.).
    - At the time, I was still a novice programmer and a novice in ML, and so a lot of the efforts were spent on learning the basics of ML and software development
    - Conclusion of the above: despite recieving an A, there was ample room for improvement.
    - Wanted to learn C++ (with high performance computing and robotics applications in mind), and so thought revizing a previous software project would be a good way to get my feet wet. In particular, my masters project involved some heavy computations, and so was a good candidate for this
    - Note: at this point, should also discuss some of the performance gains you saw
- Consider doing a mini-project related to RBMs, with an associated blog post(s) introducing RBMS, and one discussing the project

Note: could also add the IRL project to the website (don't have to make a big deal out of this --> should only take an afternoon)

In [10]:
import numpy as np

# Define the constant C
C = 0  # Change this value as needed

# Define the coefficients of the polynomial
coefficients = [1, -2, 1, C]

# Find the roots using NumPy's roots function
roots = np.roots(coefficients)

# Print the roots
print("The roots of the equation are:", roots)

i = 2
print(roots[i] ** 3 - 2* roots[i] ** 2 + roots[i] + C)

The roots of the equation are: [1.00000001 0.99999999 0.        ]
0.0
